In [1]:
using Symbolics
using RuntimeGeneratedFunctions
RuntimeGeneratedFunctions.init(@__MODULE__)

In [2]:
_prod(a, b, c, arrs...) = a .* _prod(b, c, arrs...)
_prod(a, b) = a .* b
_prod(a) = a

_prod (generic function with 3 methods)

In [3]:
function get_z_vector(dims)
    @variables q[1:dims]
    @variables p[1:dims]
    z = vcat(q,p)
    return z
end

get_z_vector (generic function with 1 method)

In [4]:
# function get_z_vector(dims, sym_arrs...)
#     z = vcat(sym_arrs...)
#     return z
# end
# d =3
# @variables q[1:d]
# @variables p[1:d]
# s = [z[i] .- z[j] for i in eachindex(z), j in eachindex(z) if i != j]
# get_z_vector(3,s)

In [4]:
# make combinations of bases of just the order that is given 
# e.g order = 2 will give just the bases whose powers sum to 2
function poly_combos(z, order, inds...)
    if order == 0
        return Num[1]
    elseif order == length(inds)
        return [_prod([z[i] for i in inds]...)]
    else
        start_ind = length(inds) == 0 ? 1 : inds[end]
        return vcat([poly_combos(z, order, inds..., j) for j in start_ind:length(z)]...)
    end
end

# gives all bases monomials up to a certain order
function primal_monomial_basis(z, order::Int)
    return Vector{Num}(vcat([poly_combos(z, i) for i in 1:order]...))
end

# calculates coefficient bases up to a certain order
# mostly for use with trigonometric functions example sin(k*z),
# where k is the coefficient
function primal_coeff_basis(z, max_coeff::Int)
    return Vector{Num}(vcat([k .* z for k in 1:max_coeff]...))
end

# calculates +,-,*,/ between states as a new basis
# the return output is a set to avoid duplicates
function primal_operator_basis(z, operator)
    return Vector{Num}([operator(z[i], z[j]) for i in 1:length(z)-1 for j in i+1:length(z)] ∪ [operator(z[j], z[i]) for i in 1:length(z)-1 for j in i+1:length(z)])
end

primal_operator_basis (generic function with 1 method)

In [7]:
function polynomial_basis(z::Vector{Num} = get_z_vector(2); polyorder::Int = 0, operator=nothing, max_coeff::Int = 0)
    primes = primal_monomial_basis(z, polyorder)
    primes = vcat(primes, primal_coeff_basis(z, max_coeff))
    if operator !== nothing
        primes = vcat(primes, primal_operator_basis(z, operator))
    end
    return primes
end

function trigonometric_basis(z::Vector{Num} = get_z_vector(2); polyorder::Int = 0, operator=nothing, max_coeff::Int = 0)
    primes = polynomial_basis(z, polyorder = polyorder, operator = operator, max_coeff = max_coeff)
    return vcat(sin.(primes), cos.(primes))
end

function exponential_basis(z::Vector{Num} = get_z_vector(2); polyorder::Int = 0, operator=nothing, max_coeff::Int = 0)
    primes = polynomial_basis(z, polyorder = polyorder, operator = operator, max_coeff = max_coeff)
    return exp.(primes)
end

function logarithmic_basis(z::Vector{Num} = get_z_vector(2); polyorder::Int = 0, operator=nothing, max_coeff::Int = 0)
    primes = polynomial_basis(z, polyorder = polyorder, operator = operator, max_coeff = max_coeff)
    return log.(primes)
end

function mixed_states_basis(bases::Vector{Num}...)
    mixed_states = Tuple(bases)
    
    ham = Vector{Num}()
    for i in eachindex(mixed_states)
        for j in i+1:lastindex(mixed_states)
            ham = vcat(ham, [mixed_states[i][k] * mixed_states[j][l] for k in 1:length(mixed_states[i]) for l in 1:length(mixed_states[j])])
        end
    end
    
    return Vector{Num}(ham)
end

mixed_states_basis (generic function with 1 method)

In [6]:
# Returns the number of required coefficients for the bases
function get_numCoeffs(basis::Vector{Num})
    return length(basis)
end

get_numCoeffs (generic function with 1 method)

In [7]:
# " gets a vector of combinations of basis"
# function get_basis(polynomial_basis, trigonometric_basis, exponential_basis, logarithmic_basis, mixed_states_basis)
#     # gets a vector of combinations of basis
#     basis = vcat(polynomial_basis, trigonometric_basis, exponential_basis, logarithmic_basis, mixed_states_basis)
#     # removes duplicates
#     basis = Vector{Num}(collect(Set(basis)))

#     return basis
# end

In [7]:
" gets a vector of combinations of basis"
function get_basis(bases::Vector{Num}...)
    # gets a vector of combinations of basis
    basis = vcat(bases...)
    
    # removes duplicates
    basis = Vector{Num}(collect(Set(basis)))

    return basis
end

get_basis

In [11]:
# function ΔH_func_builder(d; 
#     polynomial_basis::Vector{Num}=Vector{Num}(), 
#     trigonometric_basis::Vector{Num}=Vector{Num}(), 
#     exponential_basis::Vector{Num}=Vector{Num}(), 
#     logarithmic_basis::Vector{Num}=Vector{Num}(), 
#     mixed_states_basis::Vector{Num}=Vector{Num}()
#     ) 
#     # nd is the total number of dimensions of all the states, e.g. if q,p each of 3 dims, that is 6 dims in total
#     nd = 2d

#     @variables q[1:d]
#     @variables p[1:d]
#     z = vcat(q,p)
#     Dz = Differential.(z)
    
#     # collects and sums combinations of basis and coefficients"
#     basis = get_basis(polynomial_basis, trigonometric_basis, exponential_basis, logarithmic_basis, mixed_states_basis)
   
#     # gets number of terms in the basis
#     @variables a[1:get_numCoeffs(basis)]
    
#     # collect and sum combinations of basis and coefficients
#     ham = sum(collect(a .* basis))
    
#     # gives derivative of the hamiltonian, but not the skew-symmetric true one
#     f = [expand_derivatives(dz(ham)) for dz in Dz]
    
#     # line below makes the vector into a hamiltonian vector field by multiplying with the skew-symmetric matrix
#     ∇H = vcat(f[d+1:2d], -f[1:d])
    
#     # builds a function that calculates Hamiltonian gradient and converts the function to a native Julia function
#     ∇H_eval = @RuntimeGeneratedFunction(Symbolics.inject_registered_module_functions(build_function(∇H, z, a)[2]))
    
#     return ∇H_eval
# end

In [8]:
function ΔH_func_builder(d, z = get_z_vector(d), bases::Vector{Num}...) 
    # nd is the total number of dimensions of all the states, e.g. if q,p each of 3 dims, that is 6 dims in total
    nd = 2d
    Dz = Differential.(z)
    
    # collects and sums combinations of basis and coefficients"
    basis = get_basis(bases...)
   
    # gets number of terms in the basis
    @variables a[1:get_numCoeffs(basis)]
    
    # collect and sum combinations of basis and coefficients
    ham = sum(collect(a .* basis))
    
    # gives derivative of the hamiltonian, but not the skew-symmetric true one
    f = [expand_derivatives(dz(ham)) for dz in Dz]
    
    # line below makes the vector into a hamiltonian vector field by multiplying with the skew-symmetric matrix
    ∇H = vcat(f[d+1:2d], -f[1:d])
    
    # builds a function that calculates Hamiltonian gradient and converts the function to a native Julia function
    ∇H_eval = @RuntimeGeneratedFunction(Symbolics.inject_registered_module_functions(build_function(∇H, z, a)[2]))
    
    return ∇H_eval
end

ΔH_func_builder (generic function with 2 methods)

In [9]:
d = 2
z = get_z_vector(d)
z = primal_operator_basis(z, -)
polynomial = polynomial_basis(z, polyorder=0, operator = *)
trigonometric  = trigonometric_basis(z, polyorder = 1, operator = /)
logarithmic = logarithmic_basis(z, polyorder = 0, operator = -)
exponential = exponential_basis(z, polyorder=1, operator = +, max_coeff=1)
mixed_basis = mixed_states_basis(trigonometric, polynomial)
prime_mono = primal_monomial_basis(z, d)

nd = 2d
Dz = Differential.(z)

# collects and sums combinations of basis and coefficients"
basis = get_basis(prime_mono, mixed_basis)

# gets number of terms in the basis
@variables a[1:get_numCoeffs(basis)]

# collect and sum combinations of basis and coefficients
ham = sum(collect(a .* basis))

# gives derivative of the hamiltonian, but not the skew-symmetric true one
f = [expand_derivatives(dz(ham)) for dz in Dz]

# line below makes the vector into a hamiltonian vector field by multiplying with the skew-symmetric matrix
∇H = vcat(f[d+1:2d], -f[1:d])

4-element Vector{Num}:
                              (q[1] - p[1])*a[4784] + (q[2] - p[1])*a[15465] + (p[1] - p[2])*a[4302] + (q[2] - p[2])*a[14926] + (p[1] - q[2])*a[1593] + (p[2] - q[2])*a[994] + (p[1] - q[1])*a[1071] + (p[2] - p[1])*a[9226] + (q[2] - q[1])*a[3947] + (p[2] - q[1])*a[6211] + (q[1] - q[2])*a[13172] + ((q[1] - p[1])*(p[1] - q[2])*cos((q[1] - p[2]) / (p[1] - p[2]))*a[2852]) / (p[1] - p[2]) + ((p[1] - q[1])*(p[2] - q[2])*cos((q[1] - p[2]) / (q[2] - p[1]))*a[5095]) / (q[2] - p[1]) + ((p[2] - p[1])*(p[1] - q[2])*cos((q[1] - p[2]) / (q[2] - p[2]))*a[8640]) / (q[2] - p[2]) + ((p[2] - q[1])*(q[2] - q[1])*cos((q[1] - p[2]) / (p[1] - q[2]))*a[207]) / (p[1] - q[2]) + ((p[2] - p[1])*(p[2] - q[2])*cos((q[1] - p[2]) / (p[1] - q[2]))*a[16104]) / (p[1] - q[2]) + ((p[2] - p[1])*(q[2] - p[1])*cos((q[1] - p[2]) / (p[2] - q[2]))*a[170]) / (p[2] - q[2]) + ((q[1] - p[1])*(q[2] - p[1])*cos((q[1] - p[2]) / (q[1] - q[2]))*a[16664]) / (q[1] - q[2]) + ((p[2] - p[1])*(p[1] - q[2])*cos((q[1] - p[2

In [14]:
d = 2
z = get_z_vector(d)
z = primal_operator_basis(z, -)
polynomial = polynomial_basis(z, polyorder=0, operator = *)
trigonometric  = trigonometric_basis(z, polyorder = 1, operator = /)
logarithmic = logarithmic_basis(z, polyorder = 0, operator = -)
exponential = exponential_basis(z, polyorder=1, operator = +, max_coeff=1)
mixed_basis = mixed_states_basis(trigonometric, polynomial)

prime_mono = primal_monomial_basis(z, 2)
out = ΔH_func_builder(d, z,
    prime_mono, 
    exponential, 
    mixed_basis
    ) 

StackOverflowError: StackOverflowError: